<table style="width: 100%; border-style: none;">
<tr style="border-style: none">
<td style="border-style: none; width: 1%; text-align: left; font-size: 16px">Institut f&uuml;r Theoretische Physik<br /> Universit&auml;t zu K&ouml;ln</td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 16px">Prof. Dr. Simon Trebst<br />Christoph Berke</td>
</tr>
</table>
<hr>
<h1 style="font-weight:bold; text-align: center; margin: 0px; font-size: 30px; padding:0px;">Statistische Physik</h1>
<h1 style="font-weight:bold; text-align: center; margin: 0px; font-size: 30px; padding:0px;">Übungsblatt 5</h1>
<hr>
<h3 style="font-weight:bold; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px;">Wintersemester 2020/21</h3>
<hr>

**Website** [http://www.thp.uni-koeln.de/trebst/Lectures/2020-StatPhys.shtml](http://www.thp.uni-koeln.de/trebst/Lectures/2020-StatPhys.shtml)

**Abgabe**:  Montag,7.12.2020, bis 10:00 Uhr

**Besprechung**:  Dienstag, 8.12.2020

**Name**: <font color="red">Bitte geben Sie ihren Namen an</font>

**Matrikelnummer**: <font color="red">Bitte geben Sie ihre Matrikelnummer an</font>

# Die Maxwell-Verteilung des zweidimensionalen Gases

In dieser Aufgabe möchten wir zeigen, dass eine Verteilung von Gasteilchen mit Wechselwirkungen im zeitlichen Grenzwert gegen die Maxwell-Verteilung konvergiert. Sie sollen im Folgenden aus den Ihnen bekannten Bausteinen zur Simulation des zweidimensionalen Gases die Entwicklung der Geschwindigkeitsverteilung visualisieren und diskutieren.

### Animationen als Filme speichern

Im Folgenden Code geben wir Ihnen zusätzlich die Möglichkeit, die Animationen als Filme abzuspeichern. Dafür müssen Sie nur die entsprechenden Codeblöcke auskommentieren. Allerdings ist es nicht sichergestellt, dass Animationen abzuspeichern auf Ihrem Computer unterstützt wird, weshalb das Abspeichern weder erwartet noch vorausgesetzt wird um die Aufgabe zu lösen.

### Framework und Pakete

Stellen Sie zuerst sicher, dass Sie bereits alle wichtigen Julia-Pakete installiert haben und diese verwenden können. Sofern Sie die untere Box nicht mit der Ausgabe `true` ausführen können, installieren Sie fehlende Pakete und fahren Sie dann fort.

In [1]:
using Random
using LinearAlgebra
using ProgressMeter
using PyPlot

#using PyCall
#anim = pyimport("matplotlib.animation")

pygui(true)

true

Führen Sie jetzt die nachfolgenden Zellen aus. Diese definieren Funktionen, welche später für eine Simulation verwendet werden. Machen Sie sich die Wirkung der einzelnen Funktionen klar und fügen Sie ggf. Kommentare ein, falls für Sie nötig.

In [2]:
function initialize_particles!(
            x::Vector{<:Real},  y::Vector{<:Real},  # position arrays
            vx::Vector{<:Real}, vy::Vector{<:Real}, # velocity arrays
            r::Vector{<:Real},                      # particle radius array
            v::Real,                                # particle velocity
            box::NTuple{4, Float64}                 # box = (x_min, x_max, y_min, y_max)
        )
    
    # extract minimal / maximal x and y
    x_min, x_max, y_min, y_max = box
    
    # initialize each particle individually
    for i in 1:length(x)
        
        # random position with distance r to boundary
        x[i] = x_min+2*r[i] + rand()*(x_max - x_min - 2.5*r[i])
        y[i] = y_min+2*r[i] + rand()*(y_max - y_min - 2.5*r[i])
        
        # random velocity direction
        angle = rand()*2*pi
        vx[i] = cos(angle)*v
        vy[i] = sin(angle)*v
        
    end
    
end




function initialize_particles_without_overlap!(
            x::Vector{<:Real},  y::Vector{<:Real},  # position arrays
            vx::Vector{<:Real}, vy::Vector{<:Real}, # velocity arrays
            r::Vector{<:Real},                      # particle radius array
            v::Real,                                # particle velocity
            box::NTuple{4, Float64}                 # box = (x_min, x_max, y_min, y_max)
        )
    
    # extract minimal / maximal x and y
    x_min, x_max, y_min, y_max = box
    
    # initialize each particle individually
    for i in 1:length(x)
        
        # reset counter of maximal tries
        tries     = 0
        max_tries = 10000
        
        # random position with distance r to boundary and no overlap to other particles
        overlapping = true
        while overlapping
            x[i] = x_min+2*r[i] + rand()*(x_max - x_min - 2.5*r[i])
            y[i] = y_min+2*r[i] + rand()*(y_max - y_min - 2.5*r[i])
            overlapping = false
            for j in 1:i-1
                if (x[i]-x[j])^2 + (y[i]-y[j])^2 < 1.01*(r[i]+r[j])^2
                    overlapping = true
                end
            end
            tries += 1
            # maybe break loop because of maximum tries
            if tries > max_tries
                @error "Could not place particle! Exceeded $(max_tries) tries"
                return
            end
        end
        
        # random velocity direction
        angle = rand()*2*pi
        vx[i] = cos(angle)*v
        vy[i] = sin(angle)*v
        
    end
    
end

initialize_particles_without_overlap! (generic function with 1 method)

In [3]:
function move_particles!(
            x::Vector{<:Real}, y::Vector{<:Real},  # position arrays
            vx::Vector{<:Real},vy::Vector{<:Real}, # velocity arrays
            dt::Real,                              # time increment
            r::Vector{<:Real},                     # particle radius array
            box::NTuple{4, Float64}                # box = (x_min, x_max, y_min, y_max)
        )
    
    # move all particles by dt
    x .+= vx .* dt
    y .+= vy .* dt
    
    # check collision with bounding box
    for i in 1:length(x)
        # left / right
        if x[i]-r[i] < box[1]
            ddt = (x[i]-r[i])/vx[i]
            x[i] -= vx[i] * ddt
            vx[i] = abs(vx[i])
            x[i] += vx[i] * ddt
        elseif x[i]+r[i] > box[2]
            ddt = (box[2]-(x[i]+r[i]))/vx[i]
            x[i] -= vx[i] * ddt
            vx[i] = -abs(vx[i])
            x[i] += vx[i] * ddt
        end
        # up / down
        if y[i]-r[i] < box[3]
            ddt = (y[i]-r[i])/vy[i]
            y[i] += vy[i] * ddt
            vy[i] = abs(vy[i])
            y[i] -= vy[i] * ddt
        elseif y[i]+r[i] > box[4]
            ddt = (box[4]-(y[i]+r[i]))/vy[i]
            y[i] += vy[i] * ddt
            vy[i] = -abs(vy[i])
            y[i] -= vy[i] * ddt
        end
    end
end

move_particles! (generic function with 1 method)

In [4]:
function collide_particles!(
            x::Vector{<:Real}, y::Vector{<:Real},  # position arrays
            vx::Vector{<:Real},vy::Vector{<:Real}, # velocity arrays
            m::Vector{<:Real},                     # mass array
            r::Vector{<:Real},                     # particle radius array
        )
    
    # check all particle pairs (i,j) for collision
    for i in 1:length(x)
        for j in 1:i-1
            
            # particles i and j are too close --> collision
            if (x[i]-x[j])^2 + (y[i]-y[j])^2 < (r[i]+r[j])^2
                
                # determine time since impact
                ax = (x[j]-x[i])
                ay = (y[j]-y[i])
                bx = (vx[j]-vx[i])
                by = (vy[j]-vy[i])
                a2 = ax*ax + ay*ay
                b2 = bx*bx + by*by
                p = 2 * (ax*bx + ay*by) / b2
                q = (a2 - (r[i]+r[j])^2) / b2
                dt = -p/2 - sqrt(((p/2)^2) - q)
                
                # move backwarts in time by dt (dt<0)
                x[i] += vx[i] * dt
                x[j] += vx[j] * dt
                y[i] += vy[i] * dt
                y[j] += vy[j] * dt
                
                # let particles collide
                e_r = [x[j]-x[i], y[j]-y[i]]
                e_r = e_r ./ norm(e_r)
                v_i = e_r[1]*vx[i] + e_r[2]*vy[i]
                v_j = e_r[1]*vx[j] + e_r[2]*vy[j]
                v_i_p = 2*(m[i]*v_i + m[j]*v_j)/(m[i]+m[j])  -  v_i
                v_j_p = 2*(m[i]*v_i + m[j]*v_j)/(m[i]+m[j])  -  v_j
                vx[i] = vx[i] + (v_i_p - v_i)*e_r[1]
                vy[i] = vy[i] + (v_i_p - v_i)*e_r[2]
                vx[j] = vx[j] + (v_j_p - v_j)*e_r[1]
                vy[j] = vy[j] + (v_j_p - v_j)*e_r[2]
                
                # move forward again by dt (dt<0)
                x[i] -= vx[i] * dt
                x[j] -= vx[j] * dt
                y[i] -= vy[i] * dt
                y[j] -= vy[j] * dt
                
            end
            
        end
    end
    
end

collide_particles! (generic function with 1 method)

In [5]:
function color_of_velocity(v, v_min, v_max)
    return PyPlot.cm_get_cmap("magma")((v-v_min)/(v_max-v_min))
end

color_of_velocity (generic function with 1 method)

### a) Ausführen einer erster Simulation

Nachdem Sie jetzt alle Funktionen definiert haben, kommen wir zur eigentlich Simulation. Führen Sie die nachfolgende Zelle aus und erklären Sie in einem kleinen Absatz Text, wie die verschiedenen Bausteine des Frameworks zu einer kompletten Simulation zusammengesetzt werden.

In [7]:
###################
# PARAMETER
###################

# Number of particles
N = 100

# bounding box of simulation
box       = (0.0, 1.98, 0.0, 1.08)
box_start = box

# radius / velocity
radius = 0.02
v      = 0.4

# steps per frame of animation
steps_per_frame = 10
fps             = 60
animation_secs  = 15.0

# simulation time
t_max = 10.0
dt    = (t_max) / (animation_secs * fps) # (of one frame)
times = 0.0:dt:t_max

###################
# INITIAL CONDITIONS
###################

# create arrays
x  = zeros(N)
y  = zeros(N)
vx = zeros(N)
vy = zeros(N)
m  = zeros(N) .+ 1.0
r  = zeros(N) .+ radius


# initialize particles
initialize_particles_without_overlap!(x,y,vx,vy,r,v,box_start)



# setup histogram
N_bins = 100
v_max  = 1.2
p_v_min  = v_max*-0.1 # only for plotting
p_v_max  = v_max*0.6  # only for plotting
v_bins = collect(range(0, stop=v_max, length=N_bins+1))


# setup animation
fig = figure(figsize=((box[2]-box[1])*10, (box[4]-box[3])*10*1.35), dpi=50, frameon=false)

# setup particle plot
box_axis = subplot2grid((4, 1), (0, 0), rowspan=3)
fill([box[1],box[2],box[2],box[1],box[1]], [box[3],box[3],box[4],box[4],box[3]], color=(0.2,0.2,0.2), zorder=-99)
particle_circles = [plt.Circle((x[i],y[i]), radius=r[i], linewidth=0) for i in 1:N]
box_axis.add_collection(matplotlib.collections.PatchCollection(particle_circles, facecolor=[color_of_velocity(v, p_v_min, p_v_max) for v in sqrt.(vx.^2 .+ vy.^2)]))
xlim(box[1], box[2])
ylim(box[3], box[4])
box_axis.set_axis_off()
xticks([],[])
yticks([],[])


# plot histogram
hist_axis = subplot2grid((4, 1), (3, 0), rowspan=1)
vplot = hcat(copy(v_bins), copy(v_bins))
imshow(vplot', cmap="magma", zorder=-100, extent=(0,v_max,0,2.8), aspect="auto", vmin=p_v_min, vmax=p_v_max)
hist(sqrt.(vx.^2 .+ vy.^2), bins=v_bins, color=(0.9,0.9,0.9), density=true)
ylim(0,2.8)
xlim(0,v_max)
xticks([],[])
yticks([],[])

# adjust subplots
gcf().subplots_adjust(bottom=0.02, top=0.98, right=0.988, left=0.012, wspace=0.1, hspace=0.1)

# collect all velocities from substeps for better resolution
global velocities = Float64[]


###################
# ANIMATION
###################

# setup animation writer
#writer = anim.FFMpegWriter(fps=fps)
#writer.setup(fig, "maxwell_exercise_test.mp4")

# let animate
@showprogress "Animating ... " for (i,t) in enumerate(times)
    
    # access global velocity array
    global velocities
        
    # perform steps_per_frame time steps
    for j in 1:steps_per_frame
        # let particles collide with each other
        collide_particles!(x,y,vx,vy,m,r)
        # let particles move
        move_particles!(x,y,vx,vy,dt/steps_per_frame,r,box)
        # append velocities to array
        append!(velocities, sqrt.(vx.^2 .+ vy.^2))
        # check if too long
        if length(velocities) > 10*steps_per_frame*N
            velocities = velocities[end-(10*steps_per_frame*N):end]
        end
    end
    
    # set the plotting data of circles
    box_axis.collections[1].remove()
    particle_circles = [plt.Circle((x[i],y[i]), radius=r[i], linewidth=0) for i in 1:N]
    box_axis.add_collection(matplotlib.collections.PatchCollection(particle_circles, facecolor=[color_of_velocity(v, p_v_min, p_v_max) for v in sqrt.(vx.^2 .+ vy.^2)]))
        
    # maybe abort the animation
    if length(get_fignums()) == 0
        println("window closed")
        break
    end
    
    # plot histogram
    hist_axis.cla()
    imshow(vplot', cmap="magma", zorder=-100, extent=(0,v_max,0,2.8), aspect="auto", vmin=p_v_min, vmax=p_v_max)
    hist(velocities, bins=v_bins, color=(0.9,0.9,0.9), density=true)
    hist(velocities, bins=v_bins, color="k", density=true, histtype="step", linewidth=3)
    ylim(0,2.8)
    xlim(0,v_max)
    xticks([],[])
    yticks([],[])
    
    # show to user
    # pause(0.001)
    
    # write to file
    #writer.grab_frame()
    
    # maybe abort the animation
    if length(get_fignums()) == 0
        println("window closed")
        break
    end
    
end

# writer should finish animation file now
#writer.finish()

# everything finished
println("--- ALL DONE ---")
close(fig)

Animating ... 100%|█████████████████████████████████████| Time: 0:00:46


window closed
--- ALL DONE ---


### b) Nachstellen der Vorlesungs-Animationen

Wie im [Video B6](https://vimeo.com/481176526#t=2666s) der Vorlesung diskutiert, konvergiert jede anfängliche Geschwindigkeitsverteilung in einem Gas durch die Teilchenstöße gegen die Maxwell-Verteilung. Sie sollen in diesem Aufgabenteil diese Aussage nun praktisch prüfen, indem Sie Teilchen mit verschiedenen Geschwindigkeitsverteilungen initialisieren und diese in der Zeit entwickeln lassen.

Prüfen Sie konkret die folgenden Verteilungen:
1. Delta-Verteilung (Alle Teilchen haben die gleiche Geschwindigkeit)
2. Doppel-Peak Verteilung (Alle Teilchen haben entweder eine niedrige oder eine hohe Geschwindigkeit)
3. Box-Verteilung (Die Geschwindigkeiten der Teilchen sind gleichförmig verteilt)

### c) Thermalisierung

Die anfängliche Verteilung der Geschwindigkeiten konvergiert durch Stöße gegen die Maxwellverteilung. Prüfen Sie diese Aussage indem Sie Fälle mit wenigen und mit vielen Stößen konzipieren, etwa durch Änderung der Teilchenradien oder der Geschwindigkeiten. Stellen Sie zwei extreme Situationen dar und beschreiben Sie Ihre Schlussfolgerungen.